In [35]:
%pip install --upgrade pip

%pip install networkx pandas openpyxl

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [36]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import heapq
import numpy as np
import openpyxl 

In [37]:

df = pd.read_excel('./dataset/Data SC ACO.xlsx', sheet_name='Sheet1')

df['TV'] = df['Jarak (KM)'] / df['Kecepatan']

df.head()

Kode Ruas  Node From  Node To  Kode Jalan        Nama Jalan  Jarak (KM)  \
0          1        257      220           1       Raya Waru      2.101527   
1          2        220      257           1       Raya Waru      2.101527   
2          3        192      220           2  Letjend Sutoyo      0.385693   
3          4        220      192           2  Letjend Sutoyo      0.385693   
4          5        192      149           2  Letjend Sutoyo      0.795825   

   Vol max (q max)  Vol (q)  Kecepatan        TV  
0             1011      962       56.5  0.037195  
1             1014      962       56.5  0.037195  
2             4382     4000       40.0  0.009642  
3             4382     3422       40.0  0.009642  
4             2124     1658       40.0  0.019896

In [38]:
depot_df = pd.read_csv('./dataset/depot.csv')

depot_df.head()

Nama  Node  Persediaan Time Begin Time End
0  Depo 1    66         450       7:00    15:00
1  Depo 2   277         500       7:00    17:00
2  Depo 3   322         500       7:00    17:00

In [39]:
customer_df = pd.read_csv('./dataset/customer.csv')

customer_df.head()

Nama  Node  Permintaan Time Begin Time End
0  Konsumen 1     1          25       7:00     8:00
1  Konsumen 2     7          30       7:00     8:00
2  Konsumen 3    12          20       7:00     8:00
3  Konsumen 4    21          35       9:00     9:00
4  Konsumen 5    46          30       8:00    10:00

In [40]:
def time_to_decimal(time_str):
    hours, minutes = map(int, time_str.split(':'))
    return hours + minutes / 60

# Mengaplikasikan konversi waktu
depot_df['Time Begin'] = depot_df['Time Begin'].apply(time_to_decimal)
depot_df['Time End'] = depot_df['Time End'].apply(time_to_decimal)
customer_df['Time Begin'] = customer_df['Time Begin'].apply(time_to_decimal)
customer_df['Time End'] = customer_df['Time End'].apply(time_to_decimal)

In [41]:
depot_df

Nama  Node  Persediaan  Time Begin  Time End
0  Depo 1    66         450         7.0      15.0
1  Depo 2   277         500         7.0      17.0
2  Depo 3   322         500         7.0      17.0

In [42]:
customer_df.head()

Nama  Node  Permintaan  Time Begin  Time End
0  Konsumen 1     1          25         7.0       8.0
1  Konsumen 2     7          30         7.0       8.0
2  Konsumen 3    12          20         7.0       8.0
3  Konsumen 4    21          35         9.0       9.0
4  Konsumen 5    46          30         8.0      10.0

In [43]:
import networkx as nx

G = nx.Graph()

distance = {} 
tv_sum = {} 
traveled_paths = {} 

for idx, row in df.iterrows():
    print(idx, row['Node From'], row['Node To'], row['Jarak (KM)'], row['TV'])
    G.add_edge(row['Node From'], row['Node To'], 
               distance=row['Jarak (KM)'], speed=row['Kecepatan'], TV=row['TV'])

print(f"Graph memiliki {G.number_of_nodes()} nodus dan {G.number_of_edges()} ruas jalan.")
print(G)

for idx, row in customer_df.iterrows():
    node = int(row['Node'])
    path_lengths, shortest_paths = nx.single_source_dijkstra(G, node, weight='distance')
    distance[node] = path_lengths
    tv_sum[node] = {}
    traveled_paths[node] = {}
    
    for dest, path in shortest_paths.items():
        total_tv = sum(G[u][v]['TV'] for u, v in zip(path[:-1], path[1:]))
        tv_sum[node][dest] = total_tv
        traveled_paths[node][dest] = path 
    
    print(f"Distance for node {node}: {distance[node]}")
    print(f"Sum of TV for node {node}: {tv_sum[node]}")
    print(f"Traveled paths for node {node}: {traveled_paths[node]}")

for idx, row in depot_df.iterrows():
    node = int(row['Node'])
    
    path_lengths, shortest_paths = nx.single_source_dijkstra(G, node, weight='distance')
    distance[node] = path_lengths
    tv_sum[node] = {}
    traveled_paths[node] = {}
    

    for dest, path in shortest_paths.items():
        total_tv = sum(G[u][v]['TV'] for u, v in zip(path[:-1], path[1:]))
        tv_sum[node][dest] = total_tv
        traveled_paths[node][dest] = path  
    
    print(f"Distance for node {node}: {distance[node]}")
    print(f"Sum of TV for node {node}: {tv_sum[node]}")
    print(f"Traveled paths for node {node}: {traveled_paths[node]}")

print("Final distance data:", distance)
print("Final TV sum data:", tv_sum)
print("Final traveled paths data:", traveled_paths)


0 257 220 2.1015272 0.03719517168141593
1 220 257 2.1015272 0.03719517168141593
2 192 220 0.3856929 0.0096423225
3 220 192 0.3856929 0.0096423225
4 192 149 0.7958252 0.01989563
5 149 192 0.7958252 0.01989563
6 149 124 0.4301281 0.0107532025
7 124 149 0.4301281 0.0107532025
8 220 222 1.1688458 0.02068753628318584
9 222 220 1.1688458 0.02068753628318584
10 222 229 0.4786694 0.00828147750865052
11 229 235 0.5578447 0.009651292387543253
12 235 377 0.3682297 0.006370756055363322
13 377 236 0.1056195 0.0018273269896193773
14 236 222 1.2992554 0.022478467128027684
15 377 378 0.6552817 0.011337053633217993
16 378 377 0.6552817 0.011337053633217993
17 378 247 0.244266 0.0042260553633218
18 247 251 0.0611755 0.0010583996539792388
19 251 378 0.3053636 0.0052831072664359865
20 251 245 0.3997919 0.006916814878892733
21 245 263 0.2864912 0.004956595155709343
22 263 258 0.3161118 0.0054690622837370246
23 258 251 0.3379633 0.005847115916955018
24 263 379 0.8223246 0.014227069204152249
25 379 263 0.822

In [44]:
import random

In [45]:
import json

with open('klaster.json', 'r') as file:
    depo_data = json.load(file)
    
depot_starts = list(depo_data.keys())  
depot_starts = [int(start) for start in depot_starts]

depo1_start, depo2_start, depo3_start = depot_starts

depo1 = depo_data[str(depo1_start)]  
depo2 = depo_data[str(depo2_start)]  
depo3 = depo_data[str(depo3_start)]  

print(f"{depo1_start} .. {depo2_start} .. {depo3_start}")
print(depo1)
print(depo2)
print(depo3)

66 .. 277 .. 322
[62, 101, 1, 141, 113, 60, 4, 189, 174, 7, 256, 333, 235, 12, 21, 81, 39]
[296, 95, 106, 244, 175, 181, 161, 135, 205, 242, 408, 399, 292, 44, 28, 46, 254]
[376, 221, 248, 144, 400, 386, 140, 104, 402, 298, 264, 315, 210, 289, 355, 177]


In [46]:
alpha = 0.7  # pheromone influence
beta = 0.7   # visibility influence
rho = 0.3  # pheromone evaporation rate
gamma = 0.7  # global pheromone decay rate
q0 = 0.95  # exploration vs exploitation threshold
num_ants = 300  # number of ants
max_iter = 100  # max iterations


inf = float('inf')
nodes = list(depo1)
N = len(nodes)

# DEPO 1

In [47]:

LNN = 100  
tau0 = 1 / (N * LNN)  
pheromone = [[tau0 for _ in range(N)] for _ in range(N)]

def calculate_visibility(distances, depo1):
    N = len(depo1)
    visibility = []
    
    for i in range(N):
        row_visibility = []
        for j in range(N):
            if i == j:
                row_visibility.append(0)  
            else:
                node_i = depo1[i]
                node_j = depo1[j]
                distance_ij = distances.get(node_i, {}).get(node_j, float('inf'))  
                visibility_value = 1 / distance_ij if distance_ij > 0 else 0
                row_visibility.append(visibility_value)
        visibility.append(row_visibility)
    
    return visibility

visibility_depo1 = calculate_visibility(distance, depo1)


def state_transition(pheromone, visibility_depo1, current_node, unvisited):
    q = random.random()
    unvisited_list = list(unvisited)
    if q <= q0:  # Eksploitasi
        next_node = max(unvisited_list, key=lambda j: (pheromone[current_node][j] ** alpha) * (visibility_depo1[current_node][j] ** beta))
    else:  # Eksplorasi
        probabilities = [(pheromone[current_node][j] ** alpha) * (visibility_depo1[current_node][j] ** beta) for j in unvisited]
        total_prob = sum(probabilities)

        if total_prob == 0:
            next_node = random.choice(unvisited_list)
        else:
            probabilities = [p / total_prob for p in probabilities]
            next_node = random.choices(unvisited_list, probabilities)[0]

    return next_node

def local_pheromone_update(pheromone, i, j):
    pheromone[i][j] = (1 - rho) * pheromone[i][j] + rho * tau0

def global_pheromone_update(pheromone, best_solution, best_cost, iteration_best_cost, third_best_cost):
    A = third_best_cost
    B = best_cost  
    C = iteration_best_cost 
    
    if A == 0:
        print("Warning: A (third_best_cost) is zero; skipping pheromone update.")
        return

    delta_tau = ((A - B) + (A - C)) / A

    for i, j in best_solution:
        pheromone[i][j] = (1 - gamma) * pheromone[i][j] + gamma * delta_tau

def acs():
    best_solution = None
    best_cost_distance = float('inf')
    best_cost_time = float('inf')
    third_best_cost_distance = float('inf')

    for iteration in range(max_iter):
        all_solutions = []
        all_costs_distance = []
        all_costs_time = []

        for ant in range(num_ants):
            current_node = random.randint(0, N-1)
            unvisited = set(range(N)) - {current_node}
            tour = [current_node]
            total_distance = 0
            total_time = 0

            while unvisited:
                next_node = state_transition(pheromone, visibility_depo1, current_node, unvisited)
                tour.append(next_node)
                

                distance_here = distance[depo1_start][depo1[current_node]]
                total_distance += distance_here
                total_time += tv_sum[depo1_start][depo1[current_node]]  

                local_pheromone_update(pheromone, current_node, next_node)
                current_node = next_node
                unvisited.remove(next_node)
                    
            all_solutions.append(tour)
            all_costs_distance.append(total_distance)
            all_costs_time.append(total_time)
        
        sorted_costs_distance = sorted(all_costs_distance)
        iteration_best_cost_distance = sorted_costs_distance[0]
        third_best_cost_distance = sorted_costs_distance[2] if len(sorted_costs_distance) >= 3 else third_best_cost_distance

        if iteration_best_cost_distance < best_cost_distance:
            best_cost_distance = iteration_best_cost_distance
            best_solution = all_solutions[all_costs_distance.index(best_cost_distance)]
            best_cost_time = all_costs_time[all_costs_distance.index(best_cost_distance)]

        global_pheromone_update(pheromone, zip(best_solution[:-1], best_solution[1:]), best_cost_distance, iteration_best_cost_distance, third_best_cost_distance)

        # print(f"Iteration {iteration+1}: Best distance cost = {best_cost_distance} KM, Best time cost = {best_cost_time} hours")

    return best_solution, best_cost_distance, best_cost_time

best_solution, best_cost_distance, best_cost_time = acs()

best_solution_actual = [depo1[i] for i in best_solution]

complete_path = []

for i in range(len(best_solution_actual) - 1):
    start_node = best_solution_actual[i]
    end_node = best_solution_actual[i + 1]

    if start_node in traveled_paths and end_node in traveled_paths[start_node]:
        path_segment = traveled_paths[start_node][end_node]
        
        if i > 0:
            complete_path += path_segment[1:]  
        else:
            complete_path += path_segment 
    else:
        print(f"No path found between {start_node} and {end_node}.")

complete_path.insert(0, best_solution_actual[0])

complete_path_set = list(dict.fromkeys(complete_path))  

print("DEPO 1")

print(f"Best solution found: {best_solution_actual} with distance cost {best_cost_distance} KM and time cost {best_cost_time} hours")
print(f"Travel path: {complete_path_set}")


DEPO 1
Best solution found: [7, 12, 21, 4, 1, 60, 113, 189, 174, 141, 101, 62, 81, 39, 333, 256, 235] with distance cost 61.53822179999999 KM and time cost 1.2376871223741353 hours
Travel path: [7, 13, 12, 15, 21, 14, 8, 4, 5, 3, 2, 1, 6, 9, 20, 25, 60, 82, 84, 95, 106, 102, 97, 111, 108, 116, 113, 134, 173, 198, 189, 174, 164, 152, 141, 132, 123, 121, 118, 110, 117, 107, 101, 381, 77, 66, 62, 75, 81, 58, 56, 49, 39, 129, 157, 380, 234, 254, 390, 268, 289, 314, 383, 313, 315, 339, 333, 319, 305, 279, 256, 304, 322, 345, 346, 245, 251, 378, 377, 235]


# DEPO 2

In [48]:
nodes = list(depo2)
N = len(nodes)

alpha = 0.9  # pheromone influence
beta = 0.9   # visibility influence
rho = 0.1  # pheromone evaporation rate
gamma = 0.7  # global pheromone decay rate
q0 = 0.9  # exploration vs exploitation threshold
num_ants = 200  # number of ants
max_iter = 100  # max iterations

In [52]:

LNN = 100  
tau0 = 1 / (N * LNN)  
pheromone = [[tau0 for _ in range(N)] for _ in range(N)]

def calculate_visibility(distances, depo2):
    N = len(depo2)
    visibility = []
    
    for i in range(N):
        row_visibility = []
        for j in range(N):
            if i == j:
                row_visibility.append(0)  
            else:
                node_i = depo2[i]
                node_j = depo2[j]
                distance_ij = distances.get(node_i, {}).get(node_j, float('inf'))  
                visibility_value = 1 / distance_ij if distance_ij > 0 else 0 
                row_visibility.append(visibility_value)
        visibility.append(row_visibility)
    
    return visibility

visibility_depo2 = calculate_visibility(distance, depo2)


def state_transition(pheromone, visibility_depo2, current_node, unvisited):
    q = random.random()
    unvisited_list = list(unvisited)
    if q <= q0:  # Eksploitasi
        next_node = max(unvisited_list, key=lambda j: (pheromone[current_node][j] ** alpha) * (visibility_depo2[current_node][j] ** beta))
    else:  # Eksplorasi
        probabilities = [(pheromone[current_node][j] ** alpha) * (visibility_depo2[current_node][j] ** beta) for j in unvisited]
        total_prob = sum(probabilities)

        if total_prob == 0:
            next_node = random.choice(unvisited_list)
        else:
            probabilities = [p / total_prob for p in probabilities]
            next_node = random.choices(unvisited_list, probabilities)[0]

    return next_node

def local_pheromone_update(pheromone, i, j):
    pheromone[i][j] = (1 - rho) * pheromone[i][j] + rho * tau0

def global_pheromone_update(pheromone, best_solution, best_cost, iteration_best_cost, third_best_cost):
    A = third_best_cost
    B = best_cost  
    C = iteration_best_cost 
    
    if A == 0:
        print("Warning: A (third_best_cost) is zero; skipping pheromone update.")
        return

    delta_tau = ((A - B) + (A - C)) / A

    for i, j in best_solution:
        pheromone[i][j] = (1 - gamma) * pheromone[i][j] + gamma * delta_tau

def acs():
    best_solution = None
    best_cost_distance = float('inf')
    best_cost_time = float('inf')
    third_best_cost_distance = float('inf')

    for iteration in range(max_iter):
        all_solutions = []
        all_costs_distance = []
        all_costs_time = []

        for ant in range(num_ants):
            current_node = random.randint(0, N-1)
            unvisited = set(range(N)) - {current_node}
            tour = [current_node]
            total_distance = 0
            total_time = 0

            while unvisited:
                next_node = state_transition(pheromone, visibility_depo2, current_node, unvisited)
                tour.append(next_node)
                

                distance_here = distance[depo2_start][depo2[current_node]]
                total_distance += distance_here
                total_time += tv_sum[depo2_start][depo2[current_node]] 

                local_pheromone_update(pheromone, current_node, next_node)
                current_node = next_node
                unvisited.remove(next_node)
                    

            all_solutions.append(tour)
            all_costs_distance.append(total_distance)
            all_costs_time.append(total_time)
        
        sorted_costs_distance = sorted(all_costs_distance)
        iteration_best_cost_distance = sorted_costs_distance[0]
        third_best_cost_distance = sorted_costs_distance[2] if len(sorted_costs_distance) >= 3 else third_best_cost_distance

        if iteration_best_cost_distance < best_cost_distance:
            best_cost_distance = iteration_best_cost_distance
            best_solution = all_solutions[all_costs_distance.index(best_cost_distance)]
            best_cost_time = all_costs_time[all_costs_distance.index(best_cost_distance)]

        global_pheromone_update(pheromone, zip(best_solution[:-1], best_solution[1:]), best_cost_distance, iteration_best_cost_distance, third_best_cost_distance)

        # print(f"Iteration {iteration+1}: Best distance cost = {best_cost_distance} KM, Best time cost = {best_cost_time} hours")

    return best_solution, best_cost_distance, best_cost_time

best_solution, best_cost_distance, best_cost_time = acs()

best_solution_actual = [depo2[i] for i in best_solution]
complete_path = []

for i in range(len(best_solution_actual) - 1):
    start_node = best_solution_actual[i]
    end_node = best_solution_actual[i + 1]

    if start_node in traveled_paths and end_node in traveled_paths[start_node]:
        path_segment = traveled_paths[start_node][end_node]
        
        # print(f"Start node {start_node} and End node {end_node}")
        # print(path_segment)
        
        if i > 0:
            complete_path += path_segment[1:]  
        else:
            complete_path += path_segment 
    else:
        print(f"No path found between {start_node} and {end_node}.")

complete_path.insert(0, best_solution_actual[0])

complete_path_set = list(dict.fromkeys(complete_path)) 

print("DEPO 2") 

print(f"Best solution found: {best_solution_actual} with distance cost {best_cost_distance} KM and time cost {best_cost_time} hours")
print(f"Travel path: {complete_path_set}")

DEPO 2
Best solution found: [244, 205, 161, 135, 181, 399, 95, 106, 175, 242, 292, 296, 408, 46, 44, 28] with distance cost 36.84341119999999 KM and time cost 0.8131282827589439 hours
Travel path: [244, 204, 205, 206, 191, 161, 148, 146, 142, 139, 136, 135, 143, 166, 179, 181, 186, 200, 395, 260, 287, 409, 330, 335, 403, 357, 399, 334, 295, 280, 259, 223, 160, 397, 133, 126, 103, 98, 95, 106, 102, 97, 111, 108, 116, 138, 175, 178, 407, 224, 237, 242, 271, 282, 283, 292, 293, 277, 296, 338, 360, 408, 365, 342, 302, 391, 27, 30, 46, 38, 404, 51, 50, 44, 41, 32, 28]


# DEPO 3

In [50]:
nodes = list(depo3)
N = len(nodes)

alpha = 0.7  # pheromone influence
beta = 0.9   # visibility influence
rho = 0.5  # pheromone evaporation rate
gamma = 0.7  # global pheromone decay rate
q0 = 0.9  # exploration vs exploitation threshold
num_ants = 200  # number of ants
max_iter = 100  # max iterations

In [53]:

LNN = 100  
tau0 = 1 / (N * LNN)  
pheromone = [[tau0 for _ in range(N)] for _ in range(N)]

def calculate_visibility(distances, depo3):
    N = len(depo3)
    visibility = []
    
    for i in range(N):
        row_visibility = []
        for j in range(N):
            if i == j:
                row_visibility.append(0) 
            else:
                node_i = depo3[i]
                node_j = depo3[j]
                distance_ij = distances.get(node_i, {}).get(node_j, float('inf'))  
                visibility_value = 1 / distance_ij if distance_ij > 0 else 0 
                row_visibility.append(visibility_value)
        visibility.append(row_visibility)
    
    return visibility

visibility_depo3 = calculate_visibility(distance, depo3)


def state_transition(pheromone, visibility_depo3, current_node, unvisited):
    q = random.random()
    unvisited_list = list(unvisited)
    if q <= q0:  # Eksploitasi
        next_node = max(unvisited_list, key=lambda j: (pheromone[current_node][j] ** alpha) * (visibility_depo3[current_node][j] ** beta))
    else:  # Eksplorasi
        probabilities = [(pheromone[current_node][j] ** alpha) * (visibility_depo3[current_node][j] ** beta) for j in unvisited]
        total_prob = sum(probabilities)

        if total_prob == 0:
            next_node = random.choice(unvisited_list)
        else:
            probabilities = [p / total_prob for p in probabilities]
            next_node = random.choices(unvisited_list, probabilities)[0]

    return next_node

def local_pheromone_update(pheromone, i, j):
    pheromone[i][j] = (1 - rho) * pheromone[i][j] + rho * tau0

def global_pheromone_update(pheromone, best_solution, best_cost, iteration_best_cost, third_best_cost):
    A = third_best_cost
    B = best_cost  
    C = iteration_best_cost 
    
    if A == 0:
        print("Warning: A (third_best_cost) is zero; skipping pheromone update.")
        return

    delta_tau = ((A - B) + (A - C)) / A

    for i, j in best_solution:
        pheromone[i][j] = (1 - gamma) * pheromone[i][j] + gamma * delta_tau

def acs():
    best_solution = None
    best_cost_distance = float('inf')
    best_cost_time = float('inf')
    third_best_cost_distance = float('inf')

    for iteration in range(max_iter):
        all_solutions = []
        all_costs_distance = []
        all_costs_time = []

        for ant in range(num_ants):
            current_node = random.randint(0, N-1)
            unvisited = set(range(N)) - {current_node}
            tour = [current_node]
            total_distance = 0
            total_time = 0

            while unvisited:
                next_node = state_transition(pheromone, visibility_depo3, current_node, unvisited)
                tour.append(next_node)
                

                distance_here = distance[depo3_start][depo3[current_node]]
                total_distance += distance_here
                total_time += tv_sum[depo3_start][depo3[current_node]]  
                local_pheromone_update(pheromone, current_node, next_node)
                current_node = next_node
                unvisited.remove(next_node)
                    

            all_solutions.append(tour)
            all_costs_distance.append(total_distance)
            all_costs_time.append(total_time)
        
        sorted_costs_distance = sorted(all_costs_distance)
        iteration_best_cost_distance = sorted_costs_distance[0]
        third_best_cost_distance = sorted_costs_distance[2] if len(sorted_costs_distance) >= 3 else third_best_cost_distance

        if iteration_best_cost_distance < best_cost_distance:
            best_cost_distance = iteration_best_cost_distance
            best_solution = all_solutions[all_costs_distance.index(best_cost_distance)]
            best_cost_time = all_costs_time[all_costs_distance.index(best_cost_distance)]

        global_pheromone_update(pheromone, zip(best_solution[:-1], best_solution[1:]), best_cost_distance, iteration_best_cost_distance, third_best_cost_distance)

        # print(f"Iteration {iteration+1}: Best distance cost = {best_cost_distance} KM, Best time cost = {best_cost_time} hours")

    return best_solution, best_cost_distance, best_cost_time

best_solution, best_cost_distance, best_cost_time = acs()

best_solution_actual = [depo3[i] for i in best_solution]

complete_path = []

for i in range(len(best_solution_actual) - 1):
    start_node = best_solution_actual[i]
    end_node = best_solution_actual[i + 1]

    if start_node in traveled_paths and end_node in traveled_paths[start_node]:
        path_segment = traveled_paths[start_node][end_node]
        
        if i > 0:
            complete_path += path_segment[1:]  
        else:
            complete_path += path_segment 
    else:
        print(f"No path found between {start_node} and {end_node}.")

complete_path.insert(0, best_solution_actual[0])

complete_path_set = list(dict.fromkeys(complete_path))  

print("DEPO 3")

print(f"Best solution found: {best_solution_actual} with distance cost {best_cost_distance} KM and time cost {best_cost_time} hours")
print(f"Travel path: {complete_path_set}")

DEPO 3
Best solution found: [210, 221, 248, 264, 386, 289, 298, 315, 355, 400, 402, 177, 140, 376, 144, 104] with distance cost 39.10534059999999 KM and time cost 0.6999250258201706 hours
Travel path: [210, 218, 221, 238, 248, 264, 273, 386, 401, 289, 298, 382, 316, 315, 339, 341, 347, 355, 314, 268, 390, 254, 400, 228, 209, 194, 208, 402, 195, 177, 170, 140, 169, 180, 196, 213, 232, 256, 279, 305, 304, 322, 376, 154, 156, 144, 125, 114, 112, 104]
